In [1]:
from rtt_tools import dump_data
from rtt_tools.dump_data import *  # pussy died because of this wildcard import
from rtt_tools.export import *

logger = logging.getLogger(__name__)
coloredlogs.CHROOT_FILES = []
coloredlogs.install(level=logging.INFO, use_chroot=False)

In [ ]:
from rtt_tools.cleaner import Cleaner
cl = Cleaner()
cl.exp_id_low = 284942
cl.main()

In [2]:
loader = dump_data.Loader()
loader.thr_stest_load = 3000
exporter = Exporter(loader)

In [3]:
exp_id_list = list(range(260259, 260259+2000))

In [ ]:
exporter.load({'no_pvals':False, 'only_pval_cnt': True, 'experiment_ids': exp_id_list, 'is_secmargins':0}) #  'experiments': exp_id_list})
exporter.export(base_path='/tmp', fname='rtt-results-syso-diehgarder-t05-t06-full.json')
print(exporter.fname)


In [ ]:
ex_start = 261759 + 100  # original start: 260259
ex_end = 260259 + 2000
ex_step = 100

for exr in range(ex_start, ex_end, ex_step):
    loader = dump_data.Loader()
    loader.thr_stest_load = 1000
    exporter = Exporter(loader)
    exp_id_list = list(range(exr, exr + ex_step))
    
    exporter.load({'no_pvals':False, 'only_pval_cnt': False, 'experiment_ids': exp_id_list, 'is_secmargins':0}) #  'experiments': exp_id_list})
    exporter.export(base_path='/var/tmp/xklinec', fname='rtt-results-syso-diehgarder-t05-t06-%s.json' % (exr,))
    print(exporter.fname)
    

In [ ]:
exr = 262265
loader = dump_data.Loader()
loader.thr_stest_load = 1000
exporter = Exporter(loader)
exp_id_list = list(range(exr, 266975+1))

exporter.load({'no_pvals':False, 'only_pval_cnt': False, 'experiment_ids': exp_id_list, 'is_secmargins':0}) #  'experiments': exp_id_list})
exporter.export(base_path='/var/tmp/xklinec', fname='rtt-results-syso-diehgarder-t07-nist-qrng-%s.json' % (exr,))
print(exporter.fname)

In [ ]:
exr = 271496
loader = dump_data.Loader()
loader.thr_stest_load = 1000
exporter = Exporter(loader)
exp_id_list = list(range(exr, 283464+1))

exporter.load({'no_pvals':False, 'only_pval_cnt': False, 'experiment_ids': exp_id_list, 'is_secmargins':0}) #  'experiments': exp_id_list})
exporter.export(base_path='/var/tmp/xklinec', fname='rtt-results-syso-diehgarder-t08-aes-nist-%s.json' % (exr,))
print(exporter.fname)

In [ ]:
exr = 283466
loader = dump_data.Loader()
loader.thr_stest_load = 1000
exporter = Exporter(loader)
exp_id_list = list(range(exr, 284515+1))

exporter.load({'no_pvals':False, 'only_pval_cnt': False, 'experiment_ids': exp_id_list, 'is_secmargins':0}) #  'experiments': exp_id_list})
exporter.export(base_path='/var/tmp/xklinec', fname='rtt-results-syso-diehgarder-t10-aes-nist-stdconf-%s.json' % (exr,))
print(exporter.fname)

In [40]:
from rtt_tools.gen.max_rounds import FUNC_DB, FuncDb, FuncInfo

In [41]:
import json
js1 = json.load(open('/tmp/rtt-results-full9.json'))

In [104]:
js2 = json.load(open('/tmp/rtt-results-full9-ext01.json'))

In [105]:
js = js1 + js2

In [106]:
#print(json.dumps(js[2829322], indent=2))
#for rix, rec in enumerate(js):
#    if 'lowmc' in rec['data_type']:
#        print(rec['data_type'])
#     exp_info = loader.break_exp_ph4(rec['data_type'])
#     if not exp_info:
#         print('Could not parse %s' % rec['data_type'])
#         continue

In [107]:
loader = dump_data.Loader()

def exp_info_to_rec(exp_info):
    return collections.OrderedDict([
        ('tp', exp_info.fnc_type),
        ('f', exp_info.fnc_name),
        ('s', exp_info.size),
        ('m', exp_info.meth),
        ('r', exp_info.fnc_round),
        ('e', exp_info.id),
    ])

def name_to_dict(name):  # js[0]['data_type']
    exp_info = loader.break_exp_ph4(name)
    if exp_info is None or exp_info.fnc is None:
        exp_info = loader.break_exp_ph4_mpc(name)
    if exp_info is None or exp_info.fnc is None:
        return None
    return exp_info_to_rec(exp_info)


In [108]:
funtype = {}  # fun -> type
funrounds = collections.defaultdict(lambda: set())  # fun -> set of rounds tested
methsize = {}
testvariant = {}
datatype = {}
fnames = set()
test_db = collections.defaultdict(lambda: 0)
test_db_inv = collections.defaultdict(lambda: 0)
test_db_ctr = set()
tstart = time.time()

# func_name -> (meth, size) -> round -> test:var:subtest -> [pass, fail, fail]  # 3 seed results
funcres = collections.defaultdict(                   # fncname
    lambda: collections.defaultdict(                 # meth-size
        lambda: collections.defaultdict(             # round
            lambda: collections.defaultdict(         # test-variant-subtest
                lambda: collections.OrderedDict([        
                    ('info', None),
                    ('recidx', None),
                    ('exid', None),
                    ('exs', [None]*3),
                    ('exs_info', [None]*3),
])))))


for rix, rec in enumerate(js):
    data_type = rec['data_type']
    data_type = data_type.replace('stream:cipher', 'stream_cipher')
    exp_info = loader.break_exp_ph4(data_type)
    if exp_info is None or exp_info.fnc is None:
        exp_info = loader.break_exp_ph4_mpc(data_type)
    if not exp_info or not exp_info.fnc:
        print('Could not parse %s' % data_type)
        continue
    #if rix > 1000:
    #    break
        
    funtype[exp_info.fnc_name] = exp_info.fnc_type
    funrounds[exp_info.fnc_name].add(exp_info.fnc_round)

    meth_size = '%s:%s' % (exp_info.meth, exp_info.size)
    if 'testmpc' in data_type:
        meth_size = '%s:%s:%s' % (exp_info.meth, exp_info.spread, exp_info.size)
    
    methsize[meth_size] = [exp_info.meth, exp_info.size, exp_info.spread]
    cround = exp_info.fnc_round  # TODO: not always int
    datatype[data_type] = exp_info_to_rec(exp_info)
    
    test_desc = f'{rec["test"]}##[{rec["variant_type"]}][{rec["variant"]}]##[{rec["subtest_type"]}][{rec["subtest"]}]'
    testvariant[test_desc] = collections.OrderedDict([        
        ('variant_type', rec["variant_type"]),
        ('variant', rec["variant"]),
        ('variant_id', rec["variant_id"]),
        ('subtest_type', rec["subtest_type"]),
        ('subtest', rec["subtest"]),
        ('exid', rec["exid"]),
    ])
    
    test_db_ctr.add(test_desc)
    fncresrec = funcres[exp_info.fnc_name][meth_size][cround][test_desc]
    fncresrec['exid'] = rec['exid']
    fncresrec['recidx'] = rix
    fncresrec['info'] = data_type
    fncresrec['einfo'] = exp_info
    
    # iterate over subtests
    nsubs_passed = 0
    for sub in rec['subs']:
        is_passed = sub['stats'][0]['pass']
        nsubs_passed += int(is_passed)
        
    nsubs = len(rec['subs'])
    npass_ratio = nsubs_passed / nsubs
    variant_passed = npass_ratio >= 0.99  # tune this ratio! Ratio of passed subtests to consider test passed
    
    if exp_info.id >= 3:
        print(f'!! Out of range {exp_info.id} for {data_type}')
        continue
        
    fncresrec['exs'][exp_info.id] = variant_passed
    fncresrec['exs_info'][exp_info.id] = collections.OrderedDict([
        ('exid', rec['exid']),
        ('recidx', rix),
        ('info', data_type),
        ('einfo', exp_info),
        ('nsubs', nsubs),
        ('nsubsp', nsubs_passed),
        ('nsubsr', npass_ratio),
    ])
    # print('#: %s, pass: %s, pct: %2.7f' % (nsubs, nsubs_passed, 100*nsubs_passed/nsubs))
    
# Reindex tests so we have stable IDs
all_tests = sorted(list(test_db_ctr))
for ix, test in enumerate(all_tests):
    test_db[test] = ix
    test_db_inv[ix] = test
    
#print(funrounds, funtype, funcres)
#print(json.dumps(funcres, indent=2))
print('Proc1 done in %s s' % (time.time() - tstart))

Proc1 done in 359.5398485660553 s


In [121]:
# funcres["AES"]["ctr:10485760"][3]
# Analyze function -> meth-size -> round; all tests, reject if 2/3 rejected

# All experiments computed
data_type_set = set()

# func_name -> (meth, size) -> round -> {summary dict}
funcres_agg = collections.defaultdict(               # fncname
    lambda: collections.defaultdict(                 # meth-size
        lambda: collections.defaultdict(             # round        
            lambda: collections.OrderedDict([        
                ('num_tests', 0),
                ('num_rej', 0),
                ('rejects', False),
                ('lib_num_tests', 0),
                ('lib_num_rej', 0),
                ('lib_rejects', False),
                ('info', None),
                ('einfo', None),
                ('exid', None),
                ('exs_info', collections.defaultdict(lambda: collections.OrderedDict([
                    ('exids', set()),
                    ('num_tests', 0),
                    ('num_rej', 0),
                    ('lib_rejects', 0),
                    ('rejs', set()),
                    ('all_tests', set()),
                ]))),
])))) 

# Liberal thresholding - both of the above
liberal_threshold_ratio = 0.011  # at least 0.011 rejection rate
liberal_threshold_const = 3  # at least 3 tests
conservative_ratio = 0.01  # num_rej / num_tests; num_rej += 1 if the same tests was rejected at least twice; # TUNE THIS!

ignore_random_excursions = True
ignore_testmpc = False

uncomps = 0
uncomps_funcs = collections.Counter()
uncomps_set = set()
uncomps_bat = set()
rerun_cmds = collections.defaultdict(lambda: set())
nonames_set = set()

bat_map = {
    'NIST Statistical Testing Suite': '--nist_sts',
    'Dieharder': '--dieharder',
    'TestU01 Alphabit': '--tu01_alphabit',
    'TestU01 Small Crush': '--tu01_crush',
    'TestU01 Rabbit': '--tu01_rabbit',
    'TestU01 Block Alphabit': '--tu01_blockalphabit',
    'TestU01 Crush': '--tu01_crush',
    'booltest_1': '--booltest-1',
    'booltest_2': '--booltest-2',
}

expfiles = []
expfiles_path = '../ph4-01/exps-dump/__expfiles.json'
if os.path.exists(expfiles_path):
    with open(expfiles_path) as fh:
        expfiles = json.load(fh)
        
        
def find_expfile(tpl, expfiles):
    for fname in expfiles:
        if tpl in fname:
            yield fname

            
for fname in funcres:
    for meth_size in funcres[fname]:
        for cround in funcres[fname][meth_size]:
            ctests = funcres[fname][meth_size][cround]  # all tests map
            crec = funcres_agg[fname][meth_size][cround]  # resulting dict
            
            for ctest in ctests:
                data_type_set.add(ctests[ctest]["info"])
                
                for resix, resex in enumerate(ctests[ctest]['exs']):
                    if resex is None:
                        uncomps += 1
                        uncomps_funcs[fname] += 1
                        ename = ctests[ctest]["info"]
                        
                        if ignore_random_excursions and 'Random Excursions' in ctest:
                            continue
                        if ignore_testmpc and 'testmpc' in ename:
                            continue
                            
                        if '-e:' in ename:
                            ename2 = re.sub(r'-e:[\d]-', f'-e:{resix}-', ename)  # get seed run we need
                            ename2 = re.sub(r'-i:([\w]+(:?\.key)?)-.*', '-i:\\1', ename2)  # cut off input specifications
                            ename2 = re.sub(r'^PH4-SM-[\d]+-', '', ename2)  # remove testing prefix, anything goes
                            fnames = list(find_expfile('-' + ename2.replace(':', '_'), expfiles))
                            if len(fnames) == 0:
                                print(f'! no fnames found. Cfg: {fname} {meth_size} {cround} {ctest} | ename: {ename} | resix: {resix}. (Check expfiles.json)')
                                nonames_set.add(ename)
                                
                            if len(fnames) != 1:
                                print(f'- more fnames than 1 ({len(fnames)}): {fnames}, Cfg: {fname} {meth_size} {cround} {ctest} | ename: {ename} | resix: {resix}')
                                fnames.sort(key=natural_sort_key)
                                fnames = list(reversed(fnames))
                                
                            ename = fnames[0] if fnames else ename
                            ename = ename.replace('.json', '')
                            ename = ename.replace('_', ':')
                            ename = ename.replace('stream:cipher', 'stream_cipher')

                        elif 'testmpc' in ename:
                            ename = re.sub(r'-inp-([\w]+?)([\d]+)-', '-inp-\\1!XXXX', ename)
                            ename = ename.replace('!XXXX', '%02d-' % resix)
                            ename = ename.replace('.json', '')
                            ename = re.sub(r'^.*-testmpc', 'testmpc', ename)
                        
                        uncomps_set.add(ename)
                        uncomps_bat.add(ctest.split('|')[0])
                        rerun_cmds[ename].add(ctest.split('|')[0])
                        print(f'Uncomputed: {fname}-{meth_size}-{cround}-{ctest}-{ctests[ctest]["exs"]}-{ctests[ctest]["recidx"]}, ename: {ename}, orig: {ctests[ctest]["info"]}')
                    
                if None in ctests[ctest]['exs']:                    
                    # print(json.dumps(js[ctests[ctest]["recidx"]], indent=2))
                    continue
                    
                # Liberal interpretation: threshold of tests is enough to tell that we reject the generator.
                crec['lib_num_tests'] += 1
                
                # Iterating over seed variant runs for given fname-methsize-round-ctest
                exs_info = ctests[ctest]['exs_info']
                for ix, exsinfo in enumerate(exs_info):
                    if exsinfo is None:
                        continue  # test was not found for this exp.id (seed alternation)
                        
                    # Single test rejects single seed stream
                    is_rejected = int(not ctests[ctest]['exs'][ix]) if ctests[ctest]['exs'][ix] is not None else 0 
                    ecrec = crec['exs_info'][ix]  # ecrec ~ funcres_agg[fname][meth_size][cround]['exs_info'][ix]
                    ecrec['exids'].add(ctests[ctest]['exs_info'][ix]['exid'])
                    ecrec['num_tests'] += 1
                    ecrec['num_rej'] += is_rejected
                    ecrec['all_tests'].add(test_db[ctest])
                    if is_rejected:
                        ecrec['rejs'].add(test_db[ctest])
                        
                    # With each update recompute lib_rejects criteria based on the current test results.    
                    ecrec['lib_rejects'] = ecrec['num_rej'] >= liberal_threshold_const and (ecrec['num_rej'] / ecrec['num_tests']) >= liberal_threshold_ratio
                    
                    # Global liberal view, summarizind seed runs
                    crec['lib_num_tests'] += 1
                    crec['lib_num_rej'] += is_rejected
                    
                # Conservative interpretation: We reject if we can reproduce the *same test* at least 2 times. 
                # 'num_rej' is then number of tests that rejected the same input at least 2 times. 
                is_rejected = sum(ctests[ctest]['exs']) <= 1  # counting passes, 1 or less passes -> rejected (2+ rejections)
                crec['num_tests'] += 1  # +1 for each test computed for fnc-methsize-round
                crec['num_rej'] += int(is_rejected)  # +1 for each rejection by a single test for fnc-methsize-round, reproduced on 3 buckets
                crec['info'] = ctests[ctest]['info']
                crec['einfo'] = ctests[ctest]['einfo']
                crec['exid'] = ctests[ctest]['exid']

            if crec['num_tests'] == 0:
                print(f'! zero tests: {fname}-{meth_size}-{cround}')
                continue
                
            cratio = crec['num_rej'] / crec['num_tests']
            crec['rejects'] = cratio >= conservative_ratio
            crec['lib_rejects'] = sum([int(crec['exs_info'][kk]['lib_rejects']) for kk in crec['exs_info'].keys()]) > 1 # 2 or more rejects
            
            
print('\n\n\n\n\n\n\n--------------------\nUncomputed total:', uncomps, 'functions:', uncomps_funcs, ' batteries:', uncomps_bat)
for ename in sorted(list(rerun_cmds.keys())):
    fname = ename.replace(':', '_')
    fname += '.json'
    bats = sorted(list(rerun_cmds[ename]))
    ename2 = ename.replace('-SM-01-', '-SM-04-')
    ename2 = ename2.replace('-SM-02-', '-SM-04-')
    fsize = ('100' if '100MiB' in fname else '10') if 'MiB' in fname else ('100' if '100MB' in fname else '10')
    print(f"submit_experiment {' '.join([bat_map[x] for x in bats])} --name '{ename2}' --cfg '/home/debian/rtt-home/RTTWebInterface/media/predefined_configurations/{fsize}MB.json' --cryptostreams-config '{fname}'")
    
print('\n\n\n-------------------Resubmit summary:')
for ename in sorted(list(rerun_cmds.keys())):
    bats = sorted(list(rerun_cmds[ename]))
    fsize = ('100' if '100MiB' in fname else '10') if 'MiB' in fname else ('100' if '100MB' in fname else '10')
    print(f"{ename} : {' '.join([bat_map[x] for x in bats])} @ {fsize}MB")

print('\n\n\n-------------------No names sum:')
for x in sorted(list(nonames_set)):
    print(x)
    
print('-----------------\n\n\nProc2 done') 
print('Num of computed experiments: %s' % (len(data_type_set)))

Uncomputed: lowmc-s128d-ctr::104857600-1-TestU01 Small Crush|smarsa_BirthdaySpacings##[Repetitions][1]##[N|d|n|p|r|t][1|1073741824|5000000|1|0|2]-[False, None, None]-67282, ename: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr01-b16-spr--s100MB, orig: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr00-b16-spr--s100MB.json
Uncomputed: lowmc-s128d-ctr::104857600-1-TestU01 Small Crush|smarsa_BirthdaySpacings##[Repetitions][1]##[N|d|n|p|r|t][1|1073741824|5000000|1|0|2]-[False, None, None]-67282, ename: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr02-b16-spr--s100MB, orig: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr00-b16-spr--s100MB.json
Uncomputed: lowmc-s128d-ctr::104857600-1-TestU01 Small Crush|sknuth_Collision##[Repetitions][1]##[N|Sparse|d|n|r|t][1|TRUE|65536|5000000|0|2]-[False, None, None]-67283, ename: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr01-b16-spr--s100MB, orig: testmpc01-lowmc-s128d-bin-raw-r1-inp-ctr00-b16-spr--s100MB.json
Uncomputed: lowmc-s128d-ctr::104857600-1-TestU01 Small Crush|sknuth_Collis

Uncomputed: lowmc-s128d-lhw::104857600-10-TestU01 Rabbit|sspectral_Fourier3##[Bit NB|Repetitions][100000000|1]##[N|k|n|r|s][24224|12|4096|0|32]-[True, True, None]-2716323, ename: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw02-b16-w5-spr--s100MB, orig: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw01-b16-w5-spr--s100MB.json
Uncomputed: lowmc-s128d-lhw::104857600-10-TestU01 Rabbit|sstring_LongestHeadRun##[Bit NB|Repetitions][100000000|1]##[L|N|n|r|s][166656|1|600|0|32]-[True, True, None]-2716324, ename: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw02-b16-w5-spr--s100MB, orig: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw01-b16-w5-spr--s100MB.json
Uncomputed: lowmc-s128d-lhw::104857600-10-TestU01 Rabbit|sstring_PeriodsInStrings##[Bit NB|Repetitions][100000000|1]##[N|n|r|s][1|3125000|0|31]-[True, True, None]-2716325, ename: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw02-b16-w5-spr--s100MB, orig: testmpc02-lowmc-s128d-bin-raw-r10-inp-lhw01-b16-w5-spr--s100MB.json
Uncomputed: lowmc-s128d-lhw::104857600-10-Test

Uncomputed: lowmc-s128a-ctr::104857600-1-TestU01 Small Crush|smarsa_BirthdaySpacings##[Repetitions][1]##[N|d|n|p|r|t][1|1073741824|5000000|1|0|2]-[False, None, None]-54538, ename: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr01-b32-spr--s100MB, orig: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr00-b32-spr--s100MB.json
Uncomputed: lowmc-s128a-ctr::104857600-1-TestU01 Small Crush|smarsa_BirthdaySpacings##[Repetitions][1]##[N|d|n|p|r|t][1|1073741824|5000000|1|0|2]-[False, None, None]-54538, ename: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr02-b32-spr--s100MB, orig: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr00-b32-spr--s100MB.json
Uncomputed: lowmc-s128a-ctr::104857600-1-TestU01 Small Crush|sknuth_Collision##[Repetitions][1]##[N|Sparse|d|n|r|t][1|TRUE|65536|5000000|0|2]-[False, None, None]-54539, ename: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr01-b32-spr--s100MB, orig: testmpc01-lowmc-s128a-bin-raw-r1-inp-ctr00-b32-spr--s100MB.json
Uncomputed: lowmc-s128a-ctr::104857600-1-TestU01 Small Crush|sknuth_Collis

Uncomputed: lowmc-s128a-lhw::1073741824-1-TestU01 Small Crush|smarsa_BirthdaySpacings##[Repetitions][1]##[N|d|n|p|r|t][1|1073741824|5000000|1|0|2]-[None, False, False]-3657296, ename: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw00-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw02-b32-w4-spr--s1000MB-.json
Uncomputed: lowmc-s128a-lhw::1073741824-1-TestU01 Small Crush|sknuth_Collision##[Repetitions][1]##[N|Sparse|d|n|r|t][1|TRUE|65536|5000000|0|2]-[None, True, True]-3657297, ename: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw00-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw02-b32-w4-spr--s1000MB-.json
Uncomputed: lowmc-s128a-lhw::1073741824-1-TestU01 Small Crush|sknuth_Gap##[Repetitions][1]##[Alpha|Beta|N|n|r][0|0.00390625|1|200000|22]-[None, False, False]-3657298, ename: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw00-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r1-inp-lhw02-b32-w4-spr--s1000MB-.json
Uncomputed: lowmc-s128a-lhw::1073741824-1-Te

Uncomputed: lowmc-s128a-lhw::1073741824-5-NIST Statistical Testing Suite|Test for the Longest Run of Ones in a Block##[Stream count|Stream size][8000|1000000]##[][]-[True, None, None]-3550059, ename: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw02-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw00-b32-w4-spr--s1000MB-.json
Uncomputed: lowmc-s128a-lhw::1073741824-5-NIST Statistical Testing Suite|Random Binary Matrix Rank Test##[Stream count|Stream size][8000|1000000]##[][]-[True, None, None]-3550060, ename: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw01-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw00-b32-w4-spr--s1000MB-.json
Uncomputed: lowmc-s128a-lhw::1073741824-5-NIST Statistical Testing Suite|Random Binary Matrix Rank Test##[Stream count|Stream size][8000|1000000]##[][]-[True, None, None]-3550060, ename: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw02-b32-w4-spr--s1000MB-, orig: testmpc15-lowmc-s128a-bin-raw-r5-inp-lhw00-b32-w4-spr--s1000MB-.json
Uncomp

...

Uncomputed: TRIPLE-DES-rnd.key:104857600-8-Dieharder|RGB Bit Distribution Test##[N-tuple setting|P-sample count][8|15]##[][]-[False, None, False]-3930803, ename: PH4-SM-25-TRIPLE-DES-t:block-r:8-b:8-s:100MiB-e:2-i:rnd.key-168sbit-offset-2, orig: PH4-SM-25-TRIPLE-DES-t:block-r:8-b:8-s:100MiB-e:2-i:rnd.key-168sbit-offset-2
! no fnames found. Cfg: TRIPLE-DES rnd.key:104857600 8 Dieharder|RGB Bit Distribution Test##[N-tuple setting|P-sample count][9|13]##[][] | ename: PH4-SM-25-TRIPLE-DES-t:block-r:8-b:8-s:100MiB-e:2-i:rnd.key-168sbit-offset-2 | resix: 1. (Check expfiles.json)
- more fnames than 1 (0): [], Cfg: TRIPLE-DES rnd.key:104857600 8 Dieharder|RGB Bit Distribution Test##[N-tuple setting|P-sample count][9|13]##[][] | ename: PH4-SM-25-TRIPLE-DES-t:block-r:8-b:8-s:100MiB-e:2-i:rnd.key-168sbit-offset-2 | resix: 1
Uncomputed: TRIPLE-DES-rnd.key:104857600-8-Dieharder|RGB Bit Distribution Test##[N-tuple setting|P-sample count][9|13]##[][]-[False, None, False]-3930804, ename: PH4-SM-25-TRI

! no fnames found. Cfg: TEA ctr.key:104857600 6 booltest_1|v1 256-1-2##[Cfg][256-1-2]##[alpha][0.00001] | ename: PH4-SM-29-TEA-t:block-r:6-b:8-s:100MiB-e:2-i:ctr.key-128sbit-offset-2 | resix: 0. (Check expfiles.json)
- more fnames than 1 (0): [], Cfg: TEA ctr.key:104857600 6 booltest_1|v1 256-1-2##[Cfg][256-1-2]##[alpha][0.00001] | ename: PH4-SM-29-TEA-t:block-r:6-b:8-s:100MiB-e:2-i:ctr.key-128sbit-offset-2 | resix: 0
Uncomputed: TEA-ctr.key:104857600-6-booltest_1|v1 256-1-2##[Cfg][256-1-2]##[alpha][0.00001]-[None, True, True]-4537036, ename: PH4-SM-29-TEA-t:block-r:6-b:8-s:100MiB-e:2-i:ctr.key-128sbit-offset-2, orig: PH4-SM-29-TEA-t:block-r:6-b:8-s:100MiB-e:2-i:ctr.key-128sbit-offset-2
! no fnames found. Cfg: TEA ctr.key:104857600 6 booltest_1|v1 512-2-2##[Cfg][512-2-2]##[alpha][0.00001] | ename: PH4-SM-29-TEA-t:block-r:6-b:8-s:100MiB-e:2-i:ctr.key-128sbit-offset-2 | resix: 0. (Check expfiles.json)
- more fnames than 1 (0): [], Cfg: TEA ctr.key:104857600 6 booltest_1|v1 512-2-2##[Cfg]

! no fnames found. Cfg: ROAD-RUNNER-K80 ctr.key:104857600 3 booltest_1|v1 128-1-1##[Cfg][128-1-1]##[alpha][0.00001] | ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:1-i:ctr.key-80sbit-offset-1 | resix: 2. (Check expfiles.json)
- more fnames than 1 (0): [], Cfg: ROAD-RUNNER-K80 ctr.key:104857600 3 booltest_1|v1 128-1-1##[Cfg][128-1-1]##[alpha][0.00001] | ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:1-i:ctr.key-80sbit-offset-1 | resix: 2
Uncomputed: ROAD-RUNNER-K80-ctr.key:104857600-3-booltest_1|v1 128-1-1##[Cfg][128-1-1]##[alpha][0.00001]-[True, True, None]-4544138, ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:1-i:ctr.key-80sbit-offset-1, orig: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:1-i:ctr.key-80sbit-offset-1
! no fnames found. Cfg: ROAD-RUNNER-K80 ctr.key:104857600 3 booltest_1|v1 384-2-2##[Cfg][384-2-2]##[alpha][0.00001] | ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:1-i:ctr.key-80sbit-offset-1 | resix: 2. (Check

! no fnames found. Cfg: ROAD-RUNNER-K80 hw.key:104857600 3 booltest_1|v1 384-1-2##[Cfg][384-1-2]##[alpha][0.00001] | ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:2-i:hw.key-hw-80bit-hw6-offsetidx-200333466-offset-12-44-45-73-75-76-r0.67-vecsize-100166734-125.00MB | resix: 0. (Check expfiles.json)
- more fnames than 1 (0): [], Cfg: ROAD-RUNNER-K80 hw.key:104857600 3 booltest_1|v1 384-1-2##[Cfg][384-1-2]##[alpha][0.00001] | ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:2-i:hw.key-hw-80bit-hw6-offsetidx-200333466-offset-12-44-45-73-75-76-r0.67-vecsize-100166734-125.00MB | resix: 0
Uncomputed: ROAD-RUNNER-K80-hw.key:104857600-3-booltest_1|v1 384-1-2##[Cfg][384-1-2]##[alpha][0.00001]-[None, True, True]-4527839, ename: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:2-i:hw.key-hw-80bit-hw6-offsetidx-200333466-offset-12-44-45-73-75-76-r0.67-vecsize-100166734-125.00MB, orig: PH4-SM-29-ROAD-RUNNER-K80-t:block-r:3-b:8-s:100MiB-e:2-i:hw.key-hw-80bit-hw6-offsetidx








--------------------
Uncomputed total: 7025 functions: Counter({'TRIPLE-DES': 1360, 'lowmc-s128a': 945, 'lowmc-s80a': 945, 'lowmc-s80b': 945, 'SINGLE-DES': 625, 'Grain': 528, 'std_mersenne_twister': 299, 'lowmc-s128d': 152, 'lowmc-s128b': 126, 'ROAD-RUNNER-K80': 106, 'SOSEMANUK': 104, 'F-FCSR': 86, 'lowmc-s128c': 74, 'TEA': 58, 'Vision_S45a': 50, 'SERPENT': 50, 'PRINCE': 44, 'SPARX-B128': 42, 'AES': 38, 'KASUMI': 38, 'TSC-4': 36, 'Vision_S128d': 25, 'LED': 24, 'JH': 18, 'LBLOCK': 18, 'RECTANGLE-K128': 18, 'PICCOLO': 18, 'SHACAL2': 16, 'BLOWFISH': 16, 'RIPEMD160': 16, 'DECIM': 12, 'XTEA': 12, 'LEA': 12, 'ROBIN-STAR': 10, 'Salsa20': 10, 'GOST': 10, 'mimc_hash-S128': 9, 'DynamicSHA2': 8, 'RC6': 8, 'RC5-20': 8, 'RECTANGLE-K80': 8, 'SPECK': 8, 'CHASKEY': 8, 'Skein': 8, 'MD6': 8, 'ARIA': 6, 'FANTOMAS': 6, 'Lesamnta': 6, 'Luffa': 6, 'AURORA': 4, 'TWOFISH': 4, 'PRIDE': 4, 'MD5': 4, 'Hermes': 4, 'SHA3': 4, 'Tangle2': 2, 'Chacha': 2, 'Tiger': 2, 'SEED': 2, 'SHA1': 2, 'CAMELLIA': 2, 'Kecca

In [122]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

# Liberal thresholding
# TODO: compute higher rounds for liberal interpretation, e.g., Tangle has not enough
use_liberal = True
funcs_no_rounds = set(['MCSSHA3', 'Shabal'])

log_lines = []
table_lines = []
tests_to_print = set()

exids_recomp_margin = 3  # rounds a top of maximal / the latest fail; only 10 & 100 MB (faster)
exids_recompute = collections.defaultdict(  # fname
    lambda: collections.defaultdict(        # meth:size
        lambda: list()))                    # set of rounds to compute

exids_recomp_margin_1000MB = 1  # rounds a top of maximal / the latest fail
exids_recompute_1000MB = collections.defaultdict(  # fname
    lambda: collections.defaultdict(        # meth:size
        lambda: None))                      # set of rounds to compute

exids_computed_1000MB = collections.defaultdict(  # fname
    lambda: collections.defaultdict(              # meth:size
        lambda: 0))

compute_cols = collections.defaultdict(     # ftype:fname
    lambda: collections.defaultdict(        # meth:size
        lambda: list()))                    # set of rounds to compute

computed_cols = collections.defaultdict(     # ftype:fname
    lambda: collections.defaultdict(         # meth:size
        lambda: set()))                      # set of rounds to compute


def natural_sort_key(s, _nsre=re.compile('([0-9]+)')):
    return [int(text) if text.isdigit() else text.lower()
            for text in _nsre.split(s)]


for fname in sorted(funcres_agg.keys(), key=natural_sort_key):
    fname_low = fname.lower()
    
    # Find info per-fname
    fmeth = list(funcres_agg[fname].keys())
    fround = list(funcres_agg[fname][fmeth[0]].keys()) if fmeth else None
    finfo = funcres_agg[fname][fmeth[0]][fround[0]] if fround else None
    finfo = finfo['einfo'] if finfo and 'einfo' in finfo else None
        
    erec = FUNC_DB.search(fname, FuncInfo.HASH if finfo is not None and finfo.fnc_type == 'hash' else FuncInfo.CIPHER)
    if erec is None and finfo.fnc_type == 'prng':
        erec = FuncInfo(fname, FuncInfo.PRNG, 0, 1, 1)
    
    max_rounds_cur = erec.max_rounds if erec else None
    crypt_rounds_cur = erec.human_broken_rounds if erec else None
    max_rounds_cur_s = ('%3d' % max_rounds_cur) if max_rounds_cur is not None else ' - '
    crypt_rounds_cur_s = ('%3d' % crypt_rounds_cur) if crypt_rounds_cur is not None else ' - '
    max_rnd_broken = None
    max_rnd_broken_100 = None
    max_rnd_broken_meth = collections.defaultdict(lambda: 0)
    max_rnd_broken_meth_100 = collections.defaultdict(lambda: 0)
    max_rnd_meth = collections.defaultdict(lambda: 0)
    ftypename = f'{erec.ftype}:{fname}'
    
    for meth in sorted(funcres_agg[fname].keys()):
        namemeth = funcres_agg[fname][meth]
        #if '104857600' not in meth: # or 'sac:' in meth:
        #    continue
        
        h100MB = 104857600
        h1000MB = 1048576000
        meth_parts = meth.split(':')
        meth_size = int(meth_parts[-1])
        is_below_1000 = meth_size < h1000MB
        is_col_type = '.key' in meth
        
        rounds = list(namemeth.keys())
        for ix, rnd in enumerate(rounds):
            if rnd == '1-0-0':
                rounds[ix] = 1
                namemeth[1] = namemeth['1-0-0']
            if rnd == 'x':
                namemeth[1] = namemeth['x']
                rounds[ix] = 1
            if rnd is None:
                namemeth[1] = namemeth[None]
                rounds[ix] = 1
                
        rounds.sort()
        cexids = [-1]*3
        for rnd in rounds:
            crec = namemeth[rnd]
            cexid = crec['exid']
            max_rnd_meth[meth] = max(max_rnd_meth[meth], rnd)
            
            for ixx in crec['exs_info'].keys():
                cexids[ixx] = max(cexids[ixx], max(crec['exs_info'][ixx]['exids']))
            
            cur_rejects = crec['lib_rejects'] if use_liberal else crec['rejects']
            cnum_rej = crec["lib_num_rej"] if use_liberal else crec["num_rej"]
            cnum_tests = crec["lib_num_tests"] if use_liberal else crec["num_tests"]
            
            con_rejects = crec['rejects']
            con_num_rej = crec["num_rej"]
            con_num_tests = crec["num_tests"]
            
            # Conservative view on rejection - same test fails at least twice on 3 seed streams
            # Liberal: X tests per seed run. Needs to be set properly.
            if cur_rejects and (max_rnd_broken is None or rnd > max_rnd_broken):
                max_rnd_broken = rnd
                
            if cur_rejects and is_below_1000 and (max_rnd_broken_100 is None or rnd > max_rnd_broken_100):
                max_rnd_broken_100 = rnd
                    
            if cur_rejects and (max_rnd_broken_meth[meth] is None or rnd > max_rnd_broken_meth[meth]):
                max_rnd_broken_meth[meth] = rnd
            
            if cur_rejects and is_below_1000 and (max_rnd_broken_meth_100[meth] is None or rnd > max_rnd_broken_meth_100[meth]):
                max_rnd_broken_meth_100[meth] = rnd
            
            if is_col_type and is_below_1000:
                computed_cols[ftypename][meth].add(rnd)
                
            # Detailed view on which tests failed in which experiments
            # In conservative interpretation, we require the same test to fail at least twice / 3 runs.
            # 'num_rej' thus does not have to match rejected tests in particular seed run 
            # (e.g., if test IDs are disjunct, 'num_rej' is 0)
            rejs_details = ''
            if cnum_rej < 15:  # disabled for brevity
                rejs_details = []
                for kix in crec['exs_info'].keys():
                    exs_info2 = crec['exs_info'][kix]
                    rejs_details.append(sorted(list(exs_info2['rejs'])))
                rejs_details = "[" + "; ".join([", ".join(['%3d' % y for y in x]) for x in rejs_details]) + "]"
            
            conv_str = ''
            if use_liberal:
                conv_str = '; c %s (%3d/%3d)' % ('R' if con_rejects else '-', con_num_rej, con_num_tests)
            
            margin_s = ('margin: %.2f %%' % (100.0 * (1 - rnd/max_rounds_cur))) if cur_rejects and max_rounds_cur is not None else '' 
            vdict = '%s (%3d/%3d%s | %s %s max. %s) %s' % ('R' if cur_rejects else '-', cnum_rej, cnum_tests, conv_str, crypt_rounds_cur_s, max_rounds_cur_s, margin_s, rejs_details)
            irnd = rnd
            try:
                irnd = int(rnd)
            except:
                pass
            srnd = ('%4d' if isinstance(irnd, int) else '%4s') % irnd
            
            log_lines.append('%25s | %20s | %s | %s' % (fname, meth, srnd, vdict))
    
        rnd_broken = max_rnd_broken_meth[meth]
        rnd_comp = max_rnd_meth[meth]
        
        # Compute also col for block functions
        if erec.ftype == FuncInfo.CIPHER and is_below_1000 and not is_col_type:
            meth_broken = max_rnd_broken_meth_100[meth]
            orig_range = list(range(meth_broken - 1, meth_broken + 2))
            recomp_list = [x for x in orig_range if x > 0 and x <= max_rounds_cur]
            
            nmeth = f'{meth_parts[0]}.key:{":".join(meth_parts[1:])}'
            compute_cols[ftypename][nmeth] = recomp_list
            
            #if erec.stype not in (FuncInfo.STREAM, FuncInfo.MPC):
            #    nmeth = f'{meth_parts[0]}.key..inp.rnd:{":".join(meth_parts[1:])}'
            #    compute_cols[ftypename][nmeth] = recomp_list
        
        # recomp list: start with new rounds only (max computed), upper bound - either max rounds or broken + limit 
        if fname in funcs_no_rounds:
            continue
        
        if meth_size < h1000MB:
            recomp_list = list(range(max(rnd_comp + 1, rnd_broken + 1), min(max_rounds_cur + 1, max(rnd_comp + 1, rnd_broken + 1 + exids_recomp_margin)))) 
            exids_recompute[ftypename][meth] = (cexids, recomp_list)
        
        # recomp 1000MB for upper levels, new sizes
        if meth_size < h100MB:
            continue
        
        meth_1000 = ':'.join(meth_parts[:-1]) + (':%s' % h1000MB)
        recomp_list_1000MB = list(range(max(rnd_broken + 1, rnd_broken + 1), min(max_rounds_cur + 1, max(rnd_broken + 1, rnd_broken + 1 + exids_recomp_margin_1000MB)))) 
        exids_recompute_1000MB[ftypename][meth_1000] = (cexids, recomp_list_1000MB)
        
        if meth_size >= h1000MB:
            exids_computed_1000MB[ftypename][meth] = max(exids_computed_1000MB[ftypename][meth], rnd_comp)
    
    # .key generator: uf rnd.key not present, base on sac estimate
    col_meth_sizes = set([int(x.split(':')[-1]) for x in compute_cols[ftypename].keys()])
    for csize in sorted(list(col_meth_sizes)):
        rnd_mth = f'rnd.key:{csize}'
        sac_mth = f'sac.key:{csize}'
        ctr_mth = f'ctr.key:{csize}'
        if rnd_mth in compute_cols[ftypename]:
            continue
        if sac_mth in compute_cols[ftypename]:
            compute_cols[ftypename][rnd_mth] = compute_cols[ftypename][sac_mth]
        elif ctr_mth in compute_cols[ftypename]:
            compute_cols[ftypename][rnd_mth] = compute_cols[ftypename][ctr_mth]
        else:
            logger.info(f'! Cannot add rnd.key for {ftypename}')
    
    # Adapt exids_recompute_1000MB, remove already computed rounds
    for cmeth in exids_computed_1000MB[ftypename].keys():
        max_rnd = exids_computed_1000MB[ftypename][cmeth]
        if cmeth not in exids_recompute_1000MB[ftypename]:
            continue
        if exids_recompute_1000MB[ftypename][cmeth] is None:
            continue
        exids_recompute_1000MB[ftypename][cmeth][1] = [x for x in exids_recompute_1000MB[ftypename][cmeth][1] if x > max_rnd]
    
    for cmeth in computed_cols[ftypename].keys():
        compute_cols[ftypename][cmeth] = [x for x in compute_cols[ftypename][cmeth] if x not in computed_cols[ftypename][cmeth]]
    
    # comp cleanup
    for cmeth in list(exids_computed_1000MB[ftypename].keys()):
        if exids_recompute_1000MB[ftypename][cmeth] is None or len(exids_recompute_1000MB[ftypename][cmeth][1]) == 0:
            del exids_recompute_1000MB[ftypename][cmeth]
    for cmeth in list(exids_recompute[ftypename].keys()):
        if exids_recompute[ftypename][cmeth] is None or len(exids_recompute[ftypename][cmeth][1]) == 0:
            del exids_recompute[ftypename][cmeth]
    
    if max_rnd_broken is None and crypt_rounds_cur is None and max_rounds_cur is None:
        print('Skipping null %s' % fname)
        continue
    
    nfname = fname
    nfname = nfname.replace('ROAD-RUNNER-K80', 'R.RUNNER.K80')
    nfname = nfname.replace('ROAD-RUNNER-K128', 'R.RUNNER.K128')
    nfname = nfname.replace('RECTANGLE-K80', 'RECT.K80')
    nfname = nfname.replace('RECTANGLE-K128', 'RECT.K128')
    
    nfname = nfname.replace('testu01-uxorshift', 'U01.XorShift')
    nfname = nfname.replace('testu01-umrg', 'U01.UMRG')
    nfname = nfname.replace('testu01-ulcg', 'U01.ULCG')
    nfname = nfname.replace('std_subtract_with_carry', 'Std.SubCarry')
    nfname = nfname.replace('std_mersenne_twister', 'Std.MTwister')
    nfname = nfname.replace('std_lcg', 'Std.LCG')
    
    nfname = nfname.replace('mimc_hash-', 'MiMC.')
    nfname = nfname.replace('gmimc-', 'GMiMC.')
    nfname = nfname.replace('lowmc-s', 'LowMC.S')
    nfname = nfname.replace('Vision_', 'Vision.')
    nfname = nfname.replace('Starkad_', 'Starkad.')
    nfname = nfname.replace('Rescue_', 'Rescue.')
    nfname = nfname.replace('Poseidon_S128_BLS12_138', 'Poseidon.BLS12')
    nfname = nfname.replace('Poseidon_', 'Poseidon.')
    
    cline = '%s & \\boxSecMarginXX{%s}{%s}{%s}' % (nfname, max_rnd_broken or 0, max_rounds_cur or 1, crypt_rounds_cur or 0)
    table_lines.append((cline, erec))
    
    #if len(table_lines)> 10: break

    
print("\n".join(log_lines))

cols = 3
per_col = math.ceil(len(table_lines)/3.0)
sorter = lambda x: (x[1].ftype, x[1].stype, natural_sort_key(x[1].fname))
table_lines.sort(key=sorter)
ntable_lines = []

print("\n\nTable lines: ", len(table_lines), ", per col:", per_col)
# for k, g in itertools.groupby(table_lines, lambda x: (x[1].ftype)):

old_type=None
for e in table_lines:
    if (e[1].ftype, e[1].stype) != old_type:
        old_type = (e[1].ftype, e[1].stype)
        if old_type[0] == FuncInfo.HASH:
            ntable_lines.append('\\multicolumn{3}{|l|}{\\textbf{Hash functions}}')
        elif old_type[0] == FuncInfo.CIPHER and old_type[1] == 0:
            ntable_lines.append('\\multicolumn{3}{|l|}{\\textbf{Block ciphers}}')
        elif old_type[0] == FuncInfo.CIPHER and old_type[1] == 2:
            ntable_lines.append('\\multicolumn{3}{|l|}{\\textbf{Stream ciphers}}')
        elif old_type[0] == FuncInfo.CIPHER and old_type[1] == 4:
            ntable_lines.append('\\multicolumn{3}{|l|}{\\textbf{MPC ciphers}}')
        elif old_type[0] == FuncInfo.PRNG:
            ntable_lines.append('\\multicolumn{3}{|l|}{\\textbf{PRNGs}}')
        
    ntable_lines.append(e[0])

print(len(ntable_lines))
per_col = math.ceil(len(ntable_lines)/3.0)
arcols = [ntable_lines[i*per_col: (i+1)*per_col] for i in range(cols)]

for x in range(per_col):
    tup = arcols[0][x] if x < len(arcols[0]) else '& ', arcols[1][x] if x < len(arcols[1]) else '& ', arcols[2][x] if x < len(arcols[2]) else '& '
    print("& ".join(tup) + "\\\\")

#for x in range(per_col):
#    l1 =    
#print("\n".join(ntable_lines))

# Specs for adding new rounds to compute
print('-----\n\n\n Compute more rounds for 10/100:\n', json.dumps(exids_recompute))#, indent=2))    
print('-----\n\n\n Compute more rounds for 1000:\n', json.dumps(exids_recompute_1000MB))#, indent=2))         
print('-----\n\n\n Compute cols:\n', json.dumps(compute_cols))#, indent=2))

2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:gmimc-S45a
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:gmimc-S45a
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:gmimc-S128e
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:gmimc-S128e
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s80a
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s80a
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s80b
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s80b
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s128a
2021-12-01 02:41:08 aura.fi.muni.cz __main__[3371102] INFO ! Cannot add rnd.key for 2:lowmc-s128a
2021-12-01 02:41:08 aura.f

                   Abacus |         ctr:10485760 |    0 | - (  2/856; c - (  0/214) |  -  280 max. ) [;  77; 449]
                   Abacus |         ctr:10485760 |    1 | - (  2/856; c - (  0/214) |  -  280 max. ) [194; ; 191]
                   Abacus |         ctr:10485760 |    2 | - (  4/856; c - (  0/214) |  -  280 max. ) [111, 449;  11;  59]
                   Abacus |         ctr:10485760 |    3 | - (  1/856; c - (  0/214) |  -  280 max. ) [449; ; ]
                   Abacus |        ctr:104857600 |    0 | - (  4/980; c - (  0/245) |  -  280 max. ) [224, 342, 444, 480; ; ]
                   Abacus |        ctr:104857600 |    1 | - (  1/980; c - (  0/245) |  -  280 max. ) [; 471; ]
                   Abacus |        ctr:104857600 |    2 | - (  1/980; c - (  0/245) |  -  280 max. ) [ 39; ; ]
                   Abacus |        ctr:104857600 |    3 | - (  2/980; c - (  0/245) |  -  280 max. ) [448, 510; ; ]
                   Abacus |       ctr:1073741824 |    1 | - (  7/1196; c - 